In [ ]:
!pip install stable-baselines3

In [5]:

from stable_baselines3 import PPO
from stable_baselines3.common.vec_env import DummyVecEnv
from stable_baselines3.common.noise import OrnsteinUhlenbeckActionNoise
from stable_baselines3.common.callbacks import EvalCallback, StopTrainingOnRewardThreshold
import numpy as np
import pandas as pd
import gym
from gym import spaces
import warnings
import random
import copy
import os

In [6]:
df = pd.read_csv("slot_actual_trp.csv")
actual_trp_value = df['Trp'].values
# id for the output file
run_id = 1

# parameters
params = {
'no_of_actions':50,
'ad_length_upper_limit': 15,
'ad_length_lower_limit': 15,
'impression_range_upper_limit': 20,
'impression_range_lower_limit': 20,
'no_of_slots': 20,
'slot_length':15,
'trp_list':[4,3, 5],
'prob': [0.4,0.4, 0.2],
'cost_over': 0.5,
'cost_under':1,
}


discrete_value = 1

In [7]:
Ads1 = []
for i in range(params['no_of_actions']):
  Ads1.append({
      "ID"     : i+1,
      "Length" : random.randint(params['ad_length_lower_limit'], params['ad_length_upper_limit']),
      "Imp_c"  : random.randint(params['impression_range_lower_limit'], params['impression_range_upper_limit']),
      "Imp_d"  : 0,
      "Count"  : 0,
      "Stop"   : False
  })

In [8]:
Ads1 = list(filter(lambda x: x['Length'] <= params['slot_length'], Ads1))
print(Ads1)
params['no_of_actions'] = len(Ads1)

[{'ID': 1, 'Length': 15, 'Imp_c': 20, 'Imp_d': 0, 'Count': 0, 'Stop': False}, {'ID': 2, 'Length': 15, 'Imp_c': 20, 'Imp_d': 0, 'Count': 0, 'Stop': False}, {'ID': 3, 'Length': 15, 'Imp_c': 20, 'Imp_d': 0, 'Count': 0, 'Stop': False}, {'ID': 4, 'Length': 15, 'Imp_c': 20, 'Imp_d': 0, 'Count': 0, 'Stop': False}, {'ID': 5, 'Length': 15, 'Imp_c': 20, 'Imp_d': 0, 'Count': 0, 'Stop': False}, {'ID': 6, 'Length': 15, 'Imp_c': 20, 'Imp_d': 0, 'Count': 0, 'Stop': False}, {'ID': 7, 'Length': 15, 'Imp_c': 20, 'Imp_d': 0, 'Count': 0, 'Stop': False}, {'ID': 8, 'Length': 15, 'Imp_c': 20, 'Imp_d': 0, 'Count': 0, 'Stop': False}, {'ID': 9, 'Length': 15, 'Imp_c': 20, 'Imp_d': 0, 'Count': 0, 'Stop': False}, {'ID': 10, 'Length': 15, 'Imp_c': 20, 'Imp_d': 0, 'Count': 0, 'Stop': False}, {'ID': 11, 'Length': 15, 'Imp_c': 20, 'Imp_d': 0, 'Count': 0, 'Stop': False}, {'ID': 12, 'Length': 15, 'Imp_c': 20, 'Imp_d': 0, 'Count': 0, 'Stop': False}, {'ID': 13, 'Length': 15, 'Imp_c': 20, 'Imp_d': 0, 'Count': 0, 'Stop': Fa

In [9]:
# Parameters
# total number of symbols in our portfolio
ADS_DIM = len(Ads1)

In [10]:
# environment used for training
class BasicEnv(gym.Env):
    def __init__(self, Ads1, params):
        self.Ads = copy.deepcopy(Ads1)
        self.action_space = gym.spaces.Discrete(ADS_DIM)
        self.observation_space = spaces.Box(low=0, high=max([ad['Imp_c'] for ad in Ads1]),
                                            shape=(ADS_DIM,))

        self.terminal = False
        self.state = [ad['Imp_c'] for ad in Ads1]
        self.no_of_actions = params['no_of_actions']
        self.no_of_slots = params['no_of_slots']
        self.slot_length = params['slot_length']
        self.slot = 0
        self.ad_check = np.zeros(self.no_of_actions)
        self.ad_list = np.zeros(self.no_of_actions)
        self.action_memory = []
        self.req = [ad['Imp_c'] for ad in self.Ads]
        self.trp_list = params['trp_list']
        self.cost_under = params['cost_under']
        self.cost_over = params['cost_over']
        self.prob = params['prob']
        self.cost =0
        self.counter_episode=0
        self.counter=0


    def _get_state(self):
        # state = self.req
        state = [int(x / discrete_value) for x in self.req]
        return state

    def step(self, action):
        self.counter +=1
        done = False
        cost = 0
        expected_trp = 0
        underdelivery = 0
        overdelivery = 0
        a = action
        out = {"actual_underdelivery": 0, "underdelivery": 0, "actual_overdelivery": 0}
        for i in range(len(self.trp_list)):
            expected_trp += self.trp_list[i] * self.prob[i]

        if self.slot < self.no_of_slots and done == False:
            if self.ad_check[a] == 0 and self.req[a] > 0:
                self.slot_length -= self.Ads[a]["Length"]
                if self.slot_length >= 0:
                    actual_trp = actual_trp_value[self.slot]
                    out['ad_id'] = self.Ads[a]['ID']
                    out['requirement_by_ad'] = self.req[a]
                    # self.ad_check[a] = 1
                    Ad = self.Ads[a]
                    Ad["Count"] += 1
                    exp_imp = Ad.get("Length") * (expected_trp / 15.0)  # Calculating impressions for an Ad
                    out['expected_impressions'] = Ad.get("Length") * (expected_trp / 15.0)
                    self.ad_list[a] = 1

                    if exp_imp < self.req[a]:  # Underdelivery
                        # out['underdelivery'] = self.req[a] - exp_imp
                        # out['actual_underdelivery'] = (self.req[a] - Ad.get("Length") * (self.actual_trp / 15.0))
                        out['underdelivery'] = self.req[a] - exp_imp
                        new_req = (self.req[a] - Ad.get("Length")* (actual_trp/15.0))
                        if new_req > 0:
                            out['actual_underdelivery'] = new_req
                        else:
                            out['actual_overdelivery'] = abs(new_req)#   overdelivery = 0

                        self.req[a] = max(round(self.req[a] - Ad.get("Length")* (actual_trp/15.0), 2), 0)

                    elif exp_imp > self.req[a]:  # Overdelivery
                        overdelivery = exp_imp - self.req[a]
                        new_req = Ad.get("Length")* (actual_trp/15.0) - self.req[a]
                        if new_req > 0:
                          out['actual_overdelivery'] = new_req
                        else:
                          out['actual_underdelivery'] = abs(new_req)
                        underdelivery = 0
                        self.req[a] = 0
                        Ad["Stop"] = True

                    else:  # Impressions delivered is equal to Impressions committed
                        Ad["Stop"] = True
                        self.req[a] = 0
                    self.slot += 1
                    out['overdelivery'] = overdelivery
                    self.slot_length = params['slot_length']
                    cost = underdelivery * self.cost_under + overdelivery * self.cost_over
                else:
                    cost = 10000
            else:
                cost = 10000

        self.action_memory.append(out)

        if all(self.ad_check):
            if self.slot < self.no_of_slots:
                for i in range(len(self.ad_check)):
                    if self.req[i] > 0:
                        self.ad_check[i] = 0

        # check for terminal step
        if self.slot == self.no_of_slots or all(self.ad_check) or (self.cost > 10 * self.no_of_slots * 10000):

            for k in range(self.no_of_actions):
                underdelivery += self.req[k] * self.cost_under
            cost += underdelivery
            done = True
            output = pd.DataFrame(self.action_memory)
      
            output.reset_index(inplace=True)
            output2 = output[['ad_id', 'index']].copy()
            output2.rename(columns={'index': 'spot'}, inplace=True)
            output2.sort_values(by='ad_id', inplace=True)
            output2.to_csv("output_{}_2.csv".format(run_id), index=False)
            output = output[['ad_id', 'requirement_by_ad', 'expected_impressions', 'overdelivery', 'underdelivery', 
                            'actual_underdelivery', 'actual_overdelivery']].copy()
            output['zero'] = 0

            if discrete_value > 1:
              output['expected_overdelivery_with_discretizaion'] = (output['expected_impressions'] - output['requirement_by_ad'] // discrete_value * discrete_value)//discrete_value * discrete_value
              output['expected_underdelivery_with_discretizaion'] = (output['requirement_by_ad'] // discrete_value * discrete_value - output['expected_impressions'])//discrete_value * discrete_value
              output['expected_overdelivery_with_discretizaion'] = output[['expected_overdelivery_with_discretizaion', 'zero']].max(axis=1)
              output['expected_underdelivery_with_discretizaion'] = output[['expected_underdelivery_with_discretizaion', 'zero']].max(axis=1)
            else:
              output['expected_overdelivery_with_discretizaion'] = (output['expected_impressions'] - output['requirement_by_ad'])
              output['expected_underdelivery_with_discretizaion'] = (output['requirement_by_ad'] - output['expected_impressions'])
              output['expected_overdelivery_with_discretizaion'] = output[['expected_overdelivery_with_discretizaion', 'zero']].max(axis=1)
              output['expected_underdelivery_with_discretizaion'] = output[['expected_underdelivery_with_discretizaion', 'zero']].max(axis=1)
            output.drop('zero', axis=1, inplace=True)
            output.to_csv("output_{}_full.csv".format(run_id), index=False)
            output = output.groupby('ad_id').agg({'requirement_by_ad': 'max', 'expected_impressions': 'last', 'overdelivery': 'last', 'underdelivery': 'last',  
                                                  'actual_underdelivery': 'last', 'actual_overdelivery': 'last', 'expected_overdelivery_with_discretizaion': 'last', 
                                                  'expected_underdelivery_with_discretizaion': 'last'}).reset_index()
            # output = output.drop_duplicates(subset=['ad_id'], keep='last')
            
            for ad_dict in Ads1:
              if ad_dict['ID'] not in output['ad_id'].unique():
                  add = pd.DataFrame([{'actual_underdelivery': ad_dict['Imp_c'], 'underdelivery': ad_dict['Imp_c'], 'actual_overdelivery': 0, 'ad_id': 3, 'requirement_by_ad': ad_dict['Imp_c'], 'expected_impressions': 0, 'overdelivery': 0}])
                  output = pd.concat([output, add], axis=0, sort=False)
            output.rename(columns={'overdelivery': 'expected_overdelivery', 'underdelivery': 'expected_underdelivery'}, inplace=True)
            output.to_csv("output_{}_1.csv".format(run_id), index=False)



        state = self._get_state()
        print(state)
        self.cost += cost
        if done:
            print("Run completed Cost {}".format(self.cost))
            print()
        return state, -cost, done, {}


    def reset(self):
        print(self.counter)
        self.counter=0
        self.counter_episode+=1
        print(self.counter_episode)
        self.slot_length = self.slot_length
        self.slot = 0
        self.cost = 0
        self.ad_check = np.zeros(self.no_of_actions)
        self.ad_list = np.zeros(self.no_of_actions)
        self.action_memory = []

        # Generating an initial state
        state = [ad['Imp_c'] for ad in self.Ads]
        self.req = [ad['Imp_c'] for ad in self.Ads]
        return state

In [11]:
BasicEnv(Ads1, params)

In [12]:
env_train = DummyVecEnv([lambda: BasicEnv(Ads1, params)])
max_cost = sum([ad['Imp_c'] for ad in Ads1])
n_actions = len(Ads1)
eval_env = DummyVecEnv([lambda: BasicEnv(Ads1, params)])
callback_on_best = StopTrainingOnRewardThreshold(reward_threshold=-max_cost, verbose=1)
eval_callback = EvalCallback(eval_env, callback_on_new_best=callback_on_best, verbose=1, eval_freq=10000)

In [13]:
# model settings
model = PPO("MlpPolicy", env_train, verbose=1)

model.learn(total_timesteps=20000, callback=eval_callback)

model.save("drl_model")

Using cpu device
0
1
[20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 16, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20]
[20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 16, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 17, 20, 20]
[20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 16, 20, 20, 18, 20, 20, 20, 20, 20, 20, 20, 20, 17, 20, 20]
[20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 17, 20, 20, 20, 20, 20, 16, 20, 20, 18, 20, 20, 20, 20, 20, 20, 20, 20, 17, 20, 20]
[20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 16, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 17, 20, 20, 20, 20, 20, 16, 20, 20, 18, 20, 20, 20, 20, 20

[20, 20, 20, 20, 16, 10, 20, 20, 17, 20, 20, 14, 17, 16, 20, 16, 20, 20, 20, 17, 13, 16, 20, 15, 20, 20, 20, 20, 20, 16, 20, 16, 20, 20, 12, 14, 20, 20, 20, 20, 20, 20, 20, 18, 20, 20, 20, 17, 20, 20]
Run completed Cost 920.0

20
6
[20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 16, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20]
[20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 16, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 17, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20]
[20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 18, 20, 20, 20, 20, 20, 16, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 17, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20]
[20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 18, 20, 20, 20, 20, 20, 16, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 17, 20, 20, 20, 20, 20, 17, 20, 20, 20, 20, 20, 20, 20, 

[20, 20, 20, 20, 18, 20, 20, 20, 20, 20, 20, 11, 20, 20, 14, 20, 20, 10, 17, 20, 16, 20, 20, 20, 20, 20, 20, 17, 20, 20, 20, 20, 16, 20, 15, 13, 14, 20, 17, 17, 20, 20, 20, 17, 20, 16, 20, 20, 16, 16]
Run completed Cost 920.0

20
12
[20, 20, 20, 20, 20, 20, 16, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20]
[20, 20, 20, 20, 20, 20, 16, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 17, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20]
[20, 20, 20, 20, 20, 20, 16, 20, 18, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 17, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20]
[20, 20, 20, 20, 20, 20, 13, 20, 18, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 17, 20, 20, 20, 20, 20,

[16, 20, 17, 10, 20, 20, 20, 17, 20, 20, 20, 20, 16, 20, 16, 20, 17, 20, 20, 20, 20, 20, 15, 17, 20, 14, 15, 17, 20, 20, 20, 15, 20, 20, 20, 14, 20, 20, 20, 20, 16, 20, 20, 20, 10, 20, 20, 20, 18, 20]
Run completed Cost 920.0

20
18
[20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 16, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20]
[20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 16, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 17, 20, 20, 20, 20, 20, 20]
[20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 16, 20, 20, 20, 20, 20, 18, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 17, 20, 20, 20, 20, 20, 20]
[20, 20, 20, 20, 17, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 16, 20, 20, 20, 20, 20, 18, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20,

[14, 20, 20, 20, 20, 20, 20, 20, 20, 17, 20, 16, 20, 20, 15, 20, 20, 20, 17, 20, 20, 20, 20, 16, 20, 20, 20, 14, 20, 20, 16, 16, 20, 14, 20, 20, 20, 12, 20, 20, 11, 15, 16, 20, 20, 15, 20, 16, 20, 20]
Run completed Cost 920.0

20
24
[20, 16, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20]
[20, 16, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 17, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20]
[20, 16, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 17, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 18, 20, 20, 20]
[20, 16, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 17, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20,

...

[16, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20]
[16, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 17, 20]
[16, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 18, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 17, 20]
[16, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 17, 18, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 17, 20]
[16, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 16, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 17, 18, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 17,

[20, 17, 20, 20, 20, 17, 20, 12, 16, 20, 11, 20, 16, 17, 20, 20, 16, 16, 20, 15, 20, 20, 20, 20, 20, 20, 6, 20, 20, 20, 20, 20, 20, 20, 20, 18, 20, 16, 20, 20, 15, 20, 20, 20, 20, 20, 20, 20, 16, 16]
Run completed Cost 920.0

20
1007
[20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 16, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20]
[20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 16, 20, 20, 20, 20, 20, 20, 20, 20, 20, 17, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20]
[20, 20, 20, 20, 18, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 16, 20, 20, 20, 20, 20, 20, 20, 20, 20, 17, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20]
[20, 20, 20, 20, 18, 20, 20, 20, 20, 20, 17, 20, 20, 20, 20, 20, 20, 16, 20, 20, 20, 20, 20, 20, 20, 20, 20, 17, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20

[20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 17, 16, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20]
[20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 17, 16, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 18, 20]
[20, 20, 20, 20, 17, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 17, 16, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 18, 20]
[20, 20, 20, 20, 17, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 17, 16, 20, 20, 20, 20, 16, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 18, 20]
[20, 20, 20, 20, 17, 20, 20, 20, 20, 20, 20, 20, 15, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 17, 16, 20, 20, 20, 20, 16, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 18,

[20, 20, 20, 20, 20, 16, 20, 14, 14, 20, 17, 15, 16, 20, 20, 16, 11, 20, 20, 13, 16, 20, 20, 15, 20, 17, 17, 20, 20, 20, 20, 20, 14, 20, 20, 16, 20, 17, 20, 20, 20, 20, 20, 20, 20, 20, 20, 16, 20, 20]
Run completed Cost 920.0

20
1019
[20, 20, 20, 20, 20, 20, 16, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20]
[20, 20, 20, 20, 20, 20, 16, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 17, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20]
[20, 20, 20, 20, 20, 20, 16, 20, 18, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 17, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20]
[20, 20, 20, 20, 20, 20, 16, 20, 18, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 17, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 17, 20, 2

[10, 20, 20, 16, 20, 20, 20, 20, 14, 20, 20, 20, 20, 20, 20, 20, 15, 20, 20, 20, 20, 20, 20, 20, 17, 20, 20, 20, 18, 20, 17, 20, 14, 20, 16, 20, 15, 20, 16, 20, 11, 17, 20, 20, 20, 20, 16, 20, 16, 12]
Run completed Cost 920.0

20
1025
------------------------------
| time/              |       |
|    fps             | 473   |
|    iterations      | 10    |
|    time_elapsed    | 43    |
|    total_timesteps | 20480 |
------------------------------


In [14]:
total_epochs, total_penalties = 0, 0
episodes = 10

for episode in range(episodes):
    req = copy.deepcopy(Ads1)

    state = env_train.reset()
    epochs, penalties, cost = 0, 0, 0

    done = False
    Ads = copy.deepcopy(Ads1)
    i = 0

    if episode > 0:
        last_output = pd.read_csv("output_{}_1.csv".format(run_id))
    info = [{"actions_mask": [1 for i in range(ADS_DIM)]}]
    while not done:

        pred, _ = model.predict(state)
        action = np.argmax(pred)
        state, cost, done, info = env_train.step([action])
        print(state)

    if episode > 0:
        if episode == 1:
            output = pd.read_csv("output_{}_1.csv".format(run_id))

        output['actual_underdelivery'] += last_output['actual_underdelivery']
        output['actual_overdelivery'] += last_output['actual_overdelivery']

    total_penalties += penalties
    total_epochs += epochs

output['actual_underdelivery'] /= episodes
output['actual_overdelivery'] /= episodes
output.to_csv("output_{}_1.csv".format(run_id), index=False)
print(f"Results after {episodes} episodes:")
print(f"Average timesteps per episode: {total_epochs / episodes}")
print(f"Average penalties per episode: {total_penalties / episodes}")

0
1026
[16, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20]
[[16. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20.
  20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20.
  20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20.]]
[13, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20]
[[13. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20.
  20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20.
  20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20.]]
[11, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20

[0, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20]
[[ 0. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20.
  20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20.
  20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20.]]
[0, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20]
[[ 0. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20.
  20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20.
  20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20.]]
[0, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 

[0, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20]
[[ 0. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20.
  20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20.
  20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20.]]
[0, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20]
[[ 0. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20.
  20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20.
  20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20.]]
[0, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 

[0, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20]
[[ 0. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20.
  20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20.
  20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20.]]
[0, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20]
[[ 0. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20.
  20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20.
  20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20.]]
[0, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 

[0, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20]
[[ 0. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20.
  20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20.
  20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20.]]
[0, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20]
[[ 0. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20.
  20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20.
  20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20.]]
[0, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 

[0, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20]
[[ 0. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20.
  20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20.
  20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20.]]
[0, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20]
[[ 0. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20.
  20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20.
  20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20.]]
[0, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 

[0, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20]
[[ 0. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20.
  20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20.
  20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20.]]
[0, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20]
[[ 0. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20.
  20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20.
  20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20.]]
[0, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 

[0, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20]
[[ 0. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20.
  20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20.
  20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20.]]
[0, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20]
[[ 0. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20.
  20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20.
  20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20.]]
[0, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 

[0, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20]
[[ 0. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20.
  20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20.
  20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20.]]
[0, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20]
[[ 0. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20.
  20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20.
  20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20.]]
[0, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 

[0, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20]
Run completed Cost 2020980.0

208
1045
[[20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20.
  20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20.
  20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20. 20.]]
Results after 10 episodes:
Average timesteps per episode: 0.0
Average penalties per episode: 0.0
